<a href="https://colab.research.google.com/github/awaab/FraudDetection/blob/main/credit_train_tf.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This notebook follows the tutorial: https://www.tensorflow.org/tutorials/structured_data/imbalanced_data

In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

import tensorflow as tf
from tensorflow import keras

import os
import tempfile

import sklearn
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

In [2]:
df = pd.read_csv('/content/drive/MyDrive/kaggle/creditcard.csv')
df

Time         V1         V2  ...       V28  Amount  Class
0            0.0  -1.359807  -0.072781  ... -0.021053  149.62      0
1            0.0   1.191857   0.266151  ...  0.014724    2.69      0
2            1.0  -1.358354  -1.340163  ... -0.059752  378.66      0
3            1.0  -0.966272  -0.185226  ...  0.061458  123.50      0
4            2.0  -1.158233   0.877737  ...  0.215153   69.99      0
...          ...        ...        ...  ...       ...     ...    ...
284802  172786.0 -11.881118  10.071785  ...  0.823731    0.77      0
284803  172787.0  -0.732789  -0.055080  ... -0.053527   24.79      0
284804  172788.0   1.919565  -0.301254  ... -0.026561   67.88      0
284805  172788.0  -0.240440   0.530483  ...  0.104533   10.00      0
284806  172792.0  -0.533413  -0.189733  ...  0.013649  217.00      0

[284807 rows x 31 columns]

In [3]:
eps = 0.001
df['log_Ammount'] = np.log(df.pop('Amount')+eps)
#df['Time_round_24']  =df.pop('Time') % (24 * 60 * 60)
df.pop('Time')

0              0.0
1              0.0
2              1.0
3              1.0
4              2.0
            ...   
284802    172786.0
284803    172787.0
284804    172788.0
284805    172788.0
284806    172792.0
Name: Time, Length: 284807, dtype: float64

In [4]:
pos = sum(df["Class"] == 1)
neg = sum(df["Class"] == 0)

In [5]:
scaler = StandardScaler()
y = df["Class"].values
df.pop("Class")
X = scaler.fit_transform(df.values)

In [6]:
X = np.clip(X, -5, 5)

In [7]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2)

In [8]:
X_train.shape, y_train.shape

((182276, 29), (182276,))

In [9]:
METRICS = [
      keras.metrics.TruePositives(name='tp'),
      keras.metrics.FalsePositives(name='fp'),
      keras.metrics.TrueNegatives(name='tn'),
      keras.metrics.FalseNegatives(name='fn'), 
      keras.metrics.BinaryAccuracy(name='accuracy'),
      keras.metrics.Precision(name='precision'),
      keras.metrics.Recall(name='recall'),
      keras.metrics.AUC(name='auc'),
      keras.metrics.AUC(name='prc', curve='PR'), # precision-recall curve
]

In [10]:
def make_model(metrics=METRICS, output_bias=None, input_shape=X_train.shape[1],learning_rate=1e-3):
  if output_bias is not None:
    output_bias = tf.keras.initializers.Constant(output_bias)
    
  model = keras.Sequential([
          keras.layers.Dense(
          16, activation='relu',
          input_shape=(input_shape,)),
          keras.layers.Dropout(0.5),
          keras.layers.Dense(1, activation='sigmoid',bias_initializer=output_bias),
          ])

  model.compile(
      optimizer=keras.optimizers.Adam(learning_rate),
      loss=keras.losses.BinaryCrossentropy(),
      metrics=metrics)

  return model

In [11]:
EPOCHS = 100
BATCH_SIZE = 2048

early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_prc', 
    verbose=1,
    patience=10,
    mode='max',
    restore_best_weights=True)

In [12]:
model = make_model()
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 16)                480       
_________________________________________________________________
dropout (Dropout)            (None, 16)                0         
_________________________________________________________________
dense_1 (Dense)              (None, 1)                 17        
Total params: 497
Trainable params: 497
Non-trainable params: 0
_________________________________________________________________


In [13]:
def get_results(X=X_train,y=y_train,model=model):
  results = model.evaluate(X, y, batch_size=BATCH_SIZE, verbose=0)
  res = {"loss": results[0]}
  for metric, result in zip(METRICS,results[1:]):
    res[metric.name]= result
  return res

In [14]:
get_results(model=model)

{'accuracy': 0.7826976776123047,
 'auc': 0.16545388102531433,
 'fn': 298.0,
 'fp': 39311.0,
 'loss': 0.5441051125526428,
 'prc': 0.0009682351374067366,
 'precision': 0.0005085047450847924,
 'recall': 0.0628930851817131,
 'tn': 142647.0,
 'tp': 20.0}

In [15]:

# initialize to reflect imbalance in data, to minimize initial loss
initial_bias = np.log([pos/neg])
model = make_model(output_bias=initial_bias)

In [16]:
get_results(model=model)

{'accuracy': 0.8904765248298645,
 'auc': 0.4097709655761719,
 'fn': 616.0,
 'fp': 39311.0,
 'loss': 0.019731495529413223,
 'prc': 0.00133811985142529,
 'precision': 0.0005085047450847924,
 'recall': 0.03144654259085655,
 'tn': 324605.0,
 'tp': 20.0}

In [17]:
# save weights to make a fair comparison between models and different hyperparameters
initial_weights = os.path.join(tempfile.mkdtemp(), 'initial_weights')
model.save_weights(initial_weights)

In [18]:
model = make_model()
model.load_weights(initial_weights)
model.layers[-1].bias.assign([0.0])
zero_bias_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=20,
    validation_data=(X_val, y_val), 
    verbose=0)

model = make_model()
model.load_weights(initial_weights)
careful_bias_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=20,
    validation_data=(X_val, y_val), 
    verbose=0)

In [19]:
get_results(model=model)

{'accuracy': 0.9994074702262878,
 'auc': 0.9368167519569397,
 'fn': 77.0,
 'fp': 31.0,
 'loss': 0.00273539824411273,
 'prc': 0.8241196870803833,
 'precision': 0.8860294222831726,
 'recall': 0.7578616142272949,
 'tn': 181927.0,
 'tp': 241.0}

In [20]:
def plot_loss(histories, names):
  # Use a log scale on y-axis to show the wide range of values.
  fig = go.Figure()
  for history, name in zip(histories,names):
    fig.add_trace(go.Scatter(x=history.epoch, y=np.log(history.history['loss']),
                        mode='lines',
                        name=name))
  fig.show()

In [21]:
def plot_metrics(history):
  metrics = ['loss', 'prc', 'precision', 'recall']
  
  for metric in metrics:
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history[metric],
                        mode='lines',
                        name="train"))
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history[f"val_{metric}"],
                        mode='lines',
                        name="val"))
    fig.update_layout(title=metric)
    fig.show()

In [22]:
plot_loss([careful_bias_history,zero_bias_history],["careful_bias","zero_bias"])

In [23]:
model = make_model()
model.load_weights(initial_weights)
baseline_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=EPOCHS,
    callbacks=[early_stopping],
    validation_data=(X_val, y_val))

Epoch 1/100
90/90 [==============================] - 3s 16ms/step - loss: 0.0159 - tp: 259.0000 - fp: 54.0000 - tn: 363862.0000 - fn: 377.0000 - accuracy: 0.9988 - precision: 0.8275 - recall: 0.4072 - auc: 0.7821 - prc: 0.4591 - val_loss: 0.0073 - val_tp: 11.0000 - val_fp: 2.0000 - val_tn: 45488.0000 - val_fn: 68.0000 - val_accuracy: 0.9985 - val_precision: 0.8462 - val_recall: 0.1392 - val_auc: 0.8851 - val_prc: 0.6051
Epoch 2/100
90/90 [==============================] - 0s 5ms/step - loss: 0.0085 - tp: 116.0000 - fp: 23.0000 - tn: 181935.0000 - fn: 202.0000 - accuracy: 0.9988 - precision: 0.8345 - recall: 0.3648 - auc: 0.8209 - prc: 0.4406 - val_loss: 0.0048 - val_tp: 37.0000 - val_fp: 7.0000 - val_tn: 45483.0000 - val_fn: 42.0000 - val_accuracy: 0.9989 - val_precision: 0.8409 - val_recall: 0.4684 - val_auc: 0.9048 - val_prc: 0.6904
Epoch 3/100
90/90 [==============================] - 0s 5ms/step - loss: 0.0073 - tp: 146.0000 - fp: 29.0000 - tn: 181929.0000 - fn: 172.0000 - accuracy:

In [24]:
get_results(model=model)

{'accuracy': 0.9994568824768066,
 'auc': 0.949414074420929,
 'fn': 80.0,
 'fp': 19.0,
 'loss': 0.0024195921141654253,
 'prc': 0.8477925062179565,
 'precision': 0.9260700345039368,
 'recall': 0.74842768907547,
 'tn': 181939.0,
 'tp': 238.0}

In [25]:
plot_metrics(baseline_history)

In [26]:
get_results(X_test,y_test,model=model)

{'accuracy': 0.9993329048156738,
 'auc': 0.9154365062713623,
 'fn': 31.0,
 'fp': 7.0,
 'loss': 0.0034851881209760904,
 'prc': 0.7727805376052856,
 'precision': 0.9014084339141846,
 'recall': 0.6736842393875122,
 'tn': 56860.0,
 'tp': 64.0}

In [27]:
def fig_add_roc(name, labels, predictions, fig):
  fp, tp, thresh = sklearn.metrics.roc_curve(labels, predictions)
  assert len(thresh) == len(tp)
  fig.add_trace(go.Scatter(x=100*fp, y=100*tp,
                        mode="lines+markers",#+text",
                        text=thresh,
                        name=name,
                        marker=dict(
                          size=2,
                        )
  )
  )
  fig.update_layout(
      xaxis_title="False positives [%]",
      yaxis_title="True positives [%]"

  )
def plot_roc(name_lis, labels_lis, pred_lis):
  fig = go.Figure()
  for name, labels, predictions in zip(name_lis, labels_lis, pred_lis):
    fig_add_roc(name, labels, predictions, fig)
  fig.update_layout(
      yaxis_range=[70,100],
      xaxis_range=[0,30],
  )
  fig.show()

In [28]:
train_predictions_baseline = model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_baseline = model.predict(X_test, batch_size=BATCH_SIZE)

In [29]:
plot_roc(["Train","Test"],[y_train,y_test],[train_predictions_baseline,test_predictions_baseline])

### Weighed classes



In [30]:
# Scaling by total/2 helps keep the loss to a similar magnitude.
# The sum of the weights of all examples stays the same.
total = neg + pos
weight_for_0 = (1 / neg) * (total / 2.0)
weight_for_1 = (1 / pos) * (total / 2.0)

class_weight = {0: weight_for_0, 1: weight_for_1}

print('Weight for class 0: {:.2f}'.format(weight_for_0))
print('Weight for class 1: {:.2f}'.format(weight_for_1))

Weight for class 0: 0.50
Weight for class 1: 289.44


In [31]:
weighted_model = make_model()
weighted_model.load_weights(initial_weights)

weighted_history = weighted_model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=EPOCHS,
    callbacks=[early_stopping],
    validation_data=(X_val, y_val),
    # The class weights go here
    class_weight=class_weight)

Epoch 1/100
90/90 [==============================] - 4s 17ms/step - loss: 3.3229 - tp: 103.0000 - fp: 153.0000 - tn: 238672.0000 - fn: 310.0000 - accuracy: 0.9981 - precision: 0.4023 - recall: 0.2494 - auc: 0.7011 - prc: 0.2141 - val_loss: 0.0084 - val_tp: 22.0000 - val_fp: 7.0000 - val_tn: 45483.0000 - val_fn: 57.0000 - val_accuracy: 0.9986 - val_precision: 0.7586 - val_recall: 0.2785 - val_auc: 0.9234 - val_prc: 0.4479
Epoch 2/100
90/90 [==============================] - 0s 5ms/step - loss: 1.2617 - tp: 145.0000 - fp: 459.0000 - tn: 181499.0000 - fn: 173.0000 - accuracy: 0.9965 - precision: 0.2401 - recall: 0.4560 - auc: 0.8478 - prc: 0.2736 - val_loss: 0.0095 - val_tp: 59.0000 - val_fp: 14.0000 - val_tn: 45476.0000 - val_fn: 20.0000 - val_accuracy: 0.9993 - val_precision: 0.8082 - val_recall: 0.7468 - val_auc: 0.9728 - val_prc: 0.6679
Epoch 3/100
90/90 [==============================] - 0s 5ms/step - loss: 0.7562 - tp: 209.0000 - fp: 855.0000 - tn: 181103.0000 - fn: 109.0000 - accur

In [32]:
get_results(X_test,y_test,model=weighted_model)

{'accuracy': 0.997384250164032,
 'auc': 0.9314075112342834,
 'fn': 19.0,
 'fp': 130.0,
 'loss': 0.018936021253466606,
 'prc': 0.6805539131164551,
 'precision': 0.3689320385456085,
 'recall': 0.800000011920929,
 'tn': 56737.0,
 'tp': 76.0}

### Oversampling the minority class

In [33]:
y_equal_1 = y_train==1
pos_X = X_train[y_equal_1]
neg_X = X_train[~y_equal_1]

pos_y = y_train[y_equal_1]
neg_y = y_train[~y_equal_1]

ids = np.arange(len(pos_X))
choices = np.random.choice(ids, len(neg_X))

res_pos_X = pos_X[choices]
res_pos_y = pos_y[choices]

res_pos_X.shape

(181958, 29)

In [34]:
resampled_X = np.concatenate([res_pos_X, neg_X], axis=0)
resampled_y = np.concatenate([res_pos_y, neg_y], axis=0)

order = np.arange(len(resampled_y))
np.random.shuffle(order)
resampled_X = resampled_X[order]
resampled_y = resampled_y[order]

resampled_X.shape


(363916, 29)

In [35]:
resampled_model = make_model()
resampled_model.load_weights(initial_weights)

# Reset the bias to zero, since this dataset is balanced.
output_layer = resampled_model.layers[-1] 
output_layer.bias.assign([0])

resampled_history = resampled_model.fit(
    resampled_X,
    resampled_y,
    steps_per_epoch=20,
    epochs=EPOCHS*10,
    callbacks=[early_stopping],
    validation_data=(X_val,y_val))


Epoch 1/1000
20/20 [==============================] - 6s 202ms/step - loss: 2.1204 - tp: 59554.0000 - fp: 83010.0000 - tn: 155815.0000 - fn: 122499.0000 - accuracy: 0.5117 - precision: 0.4177 - recall: 0.3271 - auc: 0.4539 - prc: 0.5094 - val_loss: 0.6883 - val_tp: 19.0000 - val_fp: 20329.0000 - val_tn: 25161.0000 - val_fn: 60.0000 - val_accuracy: 0.5526 - val_precision: 9.3375e-04 - val_recall: 0.2405 - val_auc: 0.3304 - val_prc: 0.0013
Epoch 2/1000
20/20 [==============================] - 3s 148ms/step - loss: 1.3123 - tp: 93952.0000 - fp: 82535.0000 - tn: 99423.0000 - fn: 88006.0000 - accuracy: 0.5314 - precision: 0.5323 - recall: 0.5163 - auc: 0.5368 - prc: 0.6729 - val_loss: 0.6691 - val_tp: 69.0000 - val_fp: 19538.0000 - val_tn: 25952.0000 - val_fn: 10.0000 - val_accuracy: 0.5710 - val_precision: 0.0035 - val_recall: 0.8734 - val_auc: 0.8389 - val_prc: 0.1826
Epoch 3/1000
20/20 [==============================] - 3s 148ms/step - loss: 0.8797 - tp: 121810.0000 - fp: 78403.0000 - tn

In [36]:
plot_metrics(resampled_history)

In [37]:
get_results(X_test,y_test,model=resampled_model)

{'accuracy': 0.9496155381202698,
 'auc': 0.9438180327415466,
 'fn': 12.0,
 'fp': 2858.0,
 'loss': 0.25592076778411865,
 'prc': 0.705053985118866,
 'precision': 0.028221692889928818,
 'recall': 0.8736842274665833,
 'tn': 54009.0,
 'tp': 83.0}

In [38]:
train_predictions_weighted = weighted_model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_weighted = weighted_model.predict(X_test, batch_size=BATCH_SIZE)
train_predictions_resampled = resampled_model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_resampled = resampled_model.predict(X_test, batch_size=BATCH_SIZE)

In [39]:
plot_roc(["Train_baseline","Test_baseline","Train_weiged",'Test_weighed','Train_resampled','Test_resampled'],
         [y_train,y_test]*3,
         [train_predictions_baseline,test_predictions_baseline,train_predictions_weighted,test_predictions_weighted,train_predictions_resampled,test_predictions_resampled])